In [ ]:
df = pd.read_csv("Google_compiled_01012023_23032023.csv")
df.head()

In [ ]:
headline = df["headline"]
headline.head()


headline.to_csv("to_annotate.txt", index=None, header=False)

In [1]:
#import and load spacy
import spacy
from spacy.scorer import Scorer
from spacy.tokens import Doc
from spacy.training.example import Example
from spacy import displacy
from spacy.util import minibatch, compounding

import pandas as pd
import json
import re

import random
from sklearn.model_selection import train_test_split

import pickle

In [2]:
nlp=spacy.load('en_core_web_sm')

# Getting the pipeline component for ner
ner=nlp.get_pipe("ner")
ner

C:\Users\PC\anaconda3\envs\Python39\lib\site-packages\spacy\util.py:877: UserWarning: [W095] Model 'en_core_web_sm' (3.5.0) was trained with spaCy v3.5 and may not be 100% compatible with the current version (3.4.4). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [ ]:
# TRAIN_DATA2=[
#     ("""Based on the statistics from WHO and the Centers for Disease Control and Prevention,here are the five most common infectious diseases. According to current statistics, hepatitis B is the most common infectious disease in the world, affecting some 2 billion people -- that's more than one-quarter of the world's population. This disease, which is characterized by an inflammation of the liver that leads to jaundice, nausea, and fatigue, can lead to long-term complications such as cirrhosis of the liver or even liver cancer. The concern is primarily for those who carry the chronic form of the disease, which is estimated to be about 350 million people.Malaria, a mosquito-borne disease that tends to affect children the most in tropical and subtropical climates, affects more than 500 million people annually and results in anywhere between 1 million and 3 million deaths. Behind hepatitis B, it appears to be the second most-common infectious disease, and it certainly is one of the most deadly on an annual basis. Malaria, a mosquito-borne disease that tends to affect children the most in tropical and subtropical climates, affects more than 500 million people annually and results in anywhere between 1 million and 3 million deaths. Behind hepatitis B, it appears to be the second most-common infectious disease, and it certainly is one of the most deadly on an annual basis. Hepatitis C is a less common and less severe form of hepatitis, but it almost always develops into a chronic, not acute, condition, unlike hepatitis B. Although only 3 million to 4 million new cases are reported each year, some 180 million people worldwide suffer from this chronic condition, which can lead to liver cancer or cirrhosis of the liver over time. It's at times like these that we curse mosquitoes, because a very specific type of mosquito (Aedes aegypti) is responsible for the transmission of dengue to approximately 50 million people each year. Dengue is most common in Africa and Asia and thankfully occurs in only mild to moderate forms, which can cause high fever, severe headaches, and joint and muscle pain, but rarely leads to the death of the infected patient. As I mentioned previously, estimating new and ongoing cases for some of these diseases can be downright difficult, and perhaps none more so than tuberculosis. TB is caused by a bacteria found in the lungs that can cause chest pain and a bad cough, as well as lead to a number of other nasty side effects. According to WHO, it's also the second-leading global killer behind AIDS as a single infectious agent.The majority of TB-associated deaths (95%) occur in low- to middle-income countries where TB awareness and prevention simply aren't where they need to be. The good news is that TB death rates on a global basis are falling; however, there were still 8.6 million new cases of TB reported last year, and roughly one-third of the world's population carries a latent form of TB, meaning they've been infected but aren't ill and can't transmit the disease yet. """ ,
#                {"entities": [[654,661, 'DISEASE'],[1890,1896, 'DISEASE'],[2311,2323, 'DISEASE'],
#                                             [1382,1391, 'DISEASE'], [406,414, 'DISEASE'], 
#                                             [2539,2543, 'DISEASE'], [168,177, 'DISEASE'],
#                                            [2325,2327, 'DISEASE'], [518,524, 'DISEASE']]}),
    
#     ("""Story highlights First case of Zika virus found in Puerto Rico Virus is suspected in severe outbreak of newborn microcephaly in Brazil Zika is spread by same species of mosquito that carries dengue and chikungunya. Health officials in Puerto Rico reported the island s first case of Zika, a mosquito-borne virus recently linked to the rise of a serious neurological disorder among newborns in Brazil.  There is no reason for alarm, and the public should continue to take commonsense steps to avoid mosquito bites,  Puerto Rican Congressman Pedro Pierluisi said in a statement on Thursday. He added that he expects experts from the Centers for Disease Control and Prevention to visit the island in early January to educate local physicians to  properly diagnose and treat the virus.  The CDC has issued a warning to tourists traveling to Puerto Rico and other affected areas, asking them to protect themselves from the mosquitoes that spread the virus   especially pregnant women. The Aedes aegypti mosquito thrives in tropical climates and typically lives around buildings in urban areas. It is known to bite aggressively during the day, but can also attack at night, both indoors and out. It s the same mosquito that can carry yellow fever, dengue fever and chikungunya. The Aedes mosquito is an aggressive biter, especially during the day. James Gathany There is no vaccine to prevent Zika, and once infected there is no medicine to treat the virus. Symptoms typically include fever, rash, joint pain, and the red eyes of conjunctivitis. They re usually mild, and can last up to a week. Other symptoms can include muscle pain, headache, pain behind the eyes and vomiting. Symptoms typically begin three to seven days after being bitten by an infected mosquito. Brazil hard hit Zika made news recently when it was linked to a rise in microcephaly, a neurological disorder that can result in incomplete brain development in newborns. Zika first appeared in Brazil in early 2015. More than 2,400 suspected cases of microcephaly were reported last year in 20 Brazilian states, compared with 147 cases in 2014. Doctors soon discovered that most of the affected mothers reported having Zika-like symptoms during early pregnancy   mild fever, rash and headaches. Microcephaly results in babies being born with abnormally small heads that cause often serious developmental issues and sometimes early death. In Brazil, doctors are investigating 29 related infant deaths after an autopsy on November 28 found the Zika virus in a baby born with microcephaly, establishing a link between the two.  This is an unprecedented situation, unprecedented in world scientific research,  Brazil s Health Ministry said on its website. Brazilian officials have encouraged women to postpone pregnancies if at all possible. Six Brazilian states have declared a state of emergency; in Brazil s hardest-hit state, Pernambuco, more than 900 cases of microcephaly have been reported. Research continues to determine whether Zika actually causes microcephaly and further establish an association.  These are newborns who will require special attention their entire lives. It s an emotional stress that just can t be imagined,  said Angela Rocha, the pediatric infectologist at Oswaldo Cruz Hospital in Pernambuco. The spread of Zika Zika fever was first discovered in Uganda in the 1940s and has since become endemic in parts of Africa. It also spread to the South Pacific and areas of Asia, and most recently to Latin America. Because of global travel, health experts warn the virus could appear anywhere in the world. Aedes aegypti mosquitoes Christophe Simon Zika is transmitted when a mosquito bites an infected person, and then spreads the obtained virus by biting others. In theory, the Zika virus could be spread through blood transfusion, but as yet there are no documented cases, the CDC said. There is one case of possible virus transmission via sexual contact. In the CDC s travel warning, it urges tourists in Puerto Rico and other affected areas to protect themselves by wearing long-sleeved shirts and long pants that are not thin enough to bite through, staying and sleeping in air-conditioned rooms with screens on windows, and using insect repellent approved by the Environmental Protection Agency. Higher percentages of active ingredients such as DEET, Picaridin, oil of lemon eucalyptus and IR3535 protect longer, advises the CDC, and people can also purchase clothing treated with the repellent permethrin, but should not apply it directly to skin.""",
#               {"entities":[[31,41,"DISEASE"],[191,197,"DISEASE"],[202,214,"DISEASE"],[283,287,"DISEASE"],[1228,1240,"DISEASE"],
#                            [1242,1254,"DISEASE"],[1259,1271,"DISEASE"],[1387,1391,"DISEASE"],[1524,1539,"DISEASE"],[1835,1847,"DISEASE"],
#                            [2258,2270,"DISEASE"],[2505,2515,"DISEASE"],[2536,2548,"DISEASE"],[2924,2936,"DISEASE"],[2997,3001,"DISEASE"],
#                            [3018,3030,"DISEASE"]]}),
    
#     ("""\r\n(\"CNN    A genetic test used to detect common traits many people share is not reliable in identifying rare disease-causing variations, such as those that can predict breast and ovarian cancer, a new study has found. The SNP test, which stands for  single nucleotide polymorphism,  is used by direct-to-consumer DNA and ancestry companies to identify common traits such as eye color, height and proclivity toward cheek dimples and dandruff, to name a few. But when SNP tests are applied to identifying rare mutations that contribute to disease, the study found only 16% of nearly 5,000 rare mutations could be confirmed by more stringent DNA sequencing tools. When applied to mutations in BRCA1 and BRCA2 genes, which can predict a high risk for breast and ovarian cancer, the SNP test only had a positive predictive value of 4.2%, according to the study published Monday in the journal BMJ Open Access.  It seems that a very rare, disease-causing variant detected using a SNP chip is more likely to be wrong than right,  said study co-author Caroline Wright, a professor of genomic medicine at the University of Exeter in the United Kingdom, and co-author Michael Weedon, an associate professor in bioinformatics and human genetics at the University of Exeter, in an accompanying commentary to the study.  The implications of our findings are very simple: SNP chips perform poorly for detecting very rare genetic variants and the results should never be used to guide a patient s medical care, unless they have been validated,  added co-author Leigh Jackson, a lecturer in genomic medicine at Exeter, in a separate press statement. Patients were scheduling unneeded surgeries Wright told CNN the idea for the study came from anecdotal reports from fellow clinicians, who knew patients scheduled for  invasive medical procedures that were both unnecessary and unwarranted  based on what turned out to be false-positive SNP results. In what they consider to be the first large-scale study of its kind, the team decided to use the UK Biobank to test the accuracy of the SNP tests in identifying rare disease-causing genes. The Biobank is a research repository of in-depth genetic and health information from 500,000 people who live in the UK. The genes of nearly 50,000 people in the UK Biobank had undergone both SNP testing and next generation sequencing, a DNA test with high  accuracy for these rare variants,  Wright said.  This large dataset allowed us to systematically investigate the performance of SNP chips across millions of genetic variants with a wide range of frequencies, down to those present in fewer than 1 in 100,000 individuals,  wrote Wright and Weedon in the commentary. Those results were then compared to data from a small group of people in the Personal Genome Project, a non-profit global effort designed to encourage people to share their consumer genetic data for research. In that small group, the study  found that nearly every individual had at least one rare disease-causing variant that was falsely detected by the SNP chip,  Wright and Weedon wrote.DNA tests called SNP's aren't sensitive enough to correct identify rare disease-causing genes, the study said. Shutterstock  SNP s are just the wrong tool for the job when it comes to rare variants,  Wright told CNN.  They re excellent for the common variants that are present in lots of people, but the rarer the variant is, the less likely they are to be able to correctly detect it.  Quality control Does this mean that consumers should toss out the health data they ve gotten from a consumer-based DNA test? No, Wright says, because she believes credible genetic testing companies would send out any such data for more detailed sequencing before reporting the results to their customers.  I m not as concerned about the variants companies specifically report to their consumers, because they will have done additional quality control on those specific variants.  Wright said. CNN reached out to two of the largest DNA testing consumer sites, Ancestry and 23andMe. Although the AncestryHealth product was discontinued in mid-January, Ancestry spokesperson Gina Spatafore told CNN they would continue to support existing customers. Spatafore confirmed that AncestryHealth did indeed confirm any rare disease findings via a lab certified by the Center for Medicare and Medicaid Services as part of the Clinical Laboratory Improvement Amendments (CLIA) regulations.  It is true that SNP chips do not detect very rare, single-point mutations as well as sequencing can   this has been a well-known and validated fact for many years,  Spatafore said.  That s why health results provided through our AncestryHealth product are fully validated in CLIA laboratories before they are reported to our customers,  she said.  Ancestry has never reported any health finding that was not shown by a CLIA lab to be both clinically and analytically valid.  Andy Kill, communications manager for 23andMe, told CNN that the company only reported rare disease data on  three of the most well-studied  BRCA genes which  carry clear, documented risk for breast and ovarian cancer.   About 1 in 40 individuals of Ashkenazi Jewish descent has one of these three variants,  Kill told CNN. In addition, 23andMe requires users to take  a tutorial that very clearly spells out we are only testing for three of 1,000+ genetic variants, and if you do not have one of these variants to not forgo other screenings,  Kill said.  If an individual has a family history of a medical condition or other indications for clinical testing, we always recommend consulting a health care provider first,  he said. Careful with raw data Wright said her biggest concern is that studies show people often upload their raw data to third party websites that offer to further analyze their genetic makeup. When they do that, consumers may well be uploading  hundreds of thousands of other variants that haven t necessarily gone through such strict quality control.   This raw data still contain these erroneous results,  Wright said.  Some of those will be very wrong, and yet might be linked to disease.  Both Ancestry and 23andMe spokespeople told CNN they echo those concerns.  We caution all of our customers who wish to use their unvalidated raw genotypic data to not do so for any health purposes,  Spatafore said. On their website, 23andMe tells its users that if they decide to download their raw data, they should  take caution in uploading your data to any third party applications or any service outside of your 23andMe account.  Raw data should not be used for medical purposes and we do not recommend the use of third party services that claim to interpret raw data to provide health information.  Get CNN Health's weekly newsletter Sign up here to get The Results Are In with Dr. Sanjay Gupta every Tuesday from the CNN Health team. When it comes to disease risk from BRCA genes, the US Centers for Disease Control and Prevention advises that  a direct-to-consumer genetic test may not give you a complete understanding of your breast cancer risk, especially if breast cancer runs in your family.  If you think you may be at higher risk for breast cancer, it is best to work with a doctor or genetic counselor who can assess your risk, interpret your results, and build an action plan. \"),\r\n(\"CNN   Patients who receive a diagnosis of coronary heart disease are at higher risk for cognitive decline later on, a new study shows. The study, published Monday in the Journal of the American College of Cardiology, found that scores on cognitive tests   including verbal memory and orientation of time   dropped faster after patients received such a diagnosis than they did leading up to it.  This study adds to the increasing body of literature that showcases how the heart and brain work together,  said Dr. Neelum T. Aggarwal, director of research for the Rush Heart Center for Women and a cognitive neurologist at its Cardiology Cognitive Clinic. She was not involved in the study.  We are now seeing more issues related to cognitive function from heart disease as more people are living longer, and also undergoing more heart procedures, and placed on medications,  Aggarwal wrote in an email. The authors of the study say previous research on the issue has been a mixed bag, often focused on the role of conditions like strokes and sometimes showing a more rapid cognitive decline thereafter. But the new study found a longer-term impact on the brain, following up with stroke-free adults for a median of 12 years and looking at a subset who had been diagnosed with a heart attack or angina, a kind of chest pain resulting from decreased flow of blood to the heart. Heart attack patients  had a significantly faster memory decline than those with an incident angina,  the authors noted. Cardiovascular disease is thought to affect the brain in multiple ways, experts say. It could impact small blood vessels, disrupting the flow of oxygen to parts of the brain. And the link between the two could stem from common risk factors that start earlier in life, such as obesity, diabetes and high blood pressure. The new findings suggest that there could be a gradual process at play affecting blood flow and the brain, but how it works is still unclear, according to a commentary published alongside the new study by doctors at the University of Turku in Finland. Whether there could be other external factors is also unclear. For example, the authors note that they couldn t exclude the potential impact of medications and other treatments that doctors might prescribe to newly diagnosed heart disease patients.  Teasing out what contributes the most to cognitive decline may be difficult,  Aggarwal said,  as persons with heart disease have multiple medical conditions operating at the same time.  Medications are a huge factor,  she added   including whether they are taken as prescribed. Despite the changes in cognitive scores appearing  relatively small,  according to the commentary, the study authors say that  even miniscule differences in cognitive function can result in a substantially increased risk of dementia over several years.  And because no cure exists, they say, finding ways to detect, prevent and intervene early could be our best bet to address the problem, for now. Get CNN Health's weekly newsletter Sign up here to get The Results Are In with Dr. Sanjay Gupta every Tuesday from the CNN Health team. Aggarwal said there are valuable messages in the study, drawing on her own work at the Cardiology Cognitive Clinic, where her team helps patients address chronic conditions that could take their toll on brain health.  First step is to encourage patients to tell their physicians about their memory concerns,  Aggarwal said.  Often patients don t mention this.  She also encouraged doctors and patients to go over medications and be sure they re taken as prescribed, to address other possible causes like mood and sleep, and to talk about lifestyle changes that can have a positive effect on overall health.  What is good for your heart is good for your head,  Aggarwal said.\")]""",
#               {"entities":[[168,193,"DISEASE"],[5117,5144,"DISEASE"],[7078,7091,"DISEASE"],[7112,7125,"DISEASE"],[7191,7204,"DISEASE"],
#                            [7385,7407,"DISEASE"],[8097,8110,"DISEASE"],[8371,8378,"DISEASE"],[8619,8631,"DISEASE"],[8635,8641,"DISEASE"],
#                            [8717,8729,"DISEASE"],[8810,8816,"DISEASE"],[8838,8860,"DISEASE"],[9123,9131,"DISEASE"],[9634,9647,"DISEASE"],
#                            [9769,9782,"DISEASE"]]}),
#     ("""X-chromosome inactivation in mammals is regarded as an essentially random process, but the resulting somatic-cell mosaicism creates the opportunity for cell selection. In most people with red-blood-cell glucose-6-phosphate dehydrogenase (G6PD) deficiency, the enzyme-deficient phenotype is only moderately expressed in nucleated cells. However, in a small subset of hemizygous males who suffer from chronic nonspherocytic hemolytic anemia, the underlying mutations (designated class I) cause more-severe G6PD deficiency, and this might provide an opportunity for selection in heterozygous females during development. In order to test this possibility we have analyzed four heterozygotes for class I G6PD mutations  two with G6PD Portici (1178G-- > A) and two with G6PD Bari (1187C-- > T). We found that in fractionated blood cell types (including erythroid, myeloid, and lymphoid cell lineages) there was a significant excess of G6PD-normal cells. The significant concordance that we have observed in the degree of imbalance in the different blood-cell lineages indicates that a selective mechanism is likely to operate at the level of pluripotent blood stem cells. Thus, it appears that severe G6PD deficiency affects adversely the proliferation or the survival of nucleated blood cells and that this phenotypic characteristic is critical during hematopoiesis.""",
#              {"entities": [[203,254, 'DISEASE'], [399,438, 'DISEASE'], [504,519, 'DISEASE'],
#                           [1195,1210, 'DISEASE']]})
# ]
# TRAIN_DATA2

In [3]:
with open("annotations (1).json",'r', encoding="utf8") as f:
    TRAIN_DATA = json.load(f)
    print(TRAIN_DATA)

{'classes': ['DISEASE', 'LOC', 'NATIONALITY'], 'annotations': [['Objective disease activity assessment and therapeutic drug monitoring prior to biologic therapy changes in routine inflammatory bowel disease clinical practice: TARGET-IBD - BMC Gastroenterology\r', {'entities': [[115, 141, 'DISEASE']]}], ["Crohn's disease and dietary fiber: What is the link?\r", {'entities': [[0, 15, 'DISEASE']]}], ["Northampton parents' plea over toddler with rare disease\r", {'entities': [[0, 11, 'LOC']]}], ['"\'Door has been opened\' with Rare Disease Drug Strategy, says advocate"\r', {'entities': []}], ['Is IBD an Autoimmune Disease?\r', {'entities': [[3, 6, 'DISEASE'], [10, 28, 'DISEASE']]}], ['EXCLUSIVE WHO says it advised Ukraine to destroy pathogens in health labs to prevent disease spread\r', {'entities': [[30, 37, 'LOC']]}], ['"Nutrition is the number one cause of disease, cardiologist says"\r', {'entities': []}], ['Cholesterol And Heart Disease: Is There A Connection?\r', {'entities': [[0, 11,

In [4]:
x_train ,x_test = train_test_split(TRAIN_DATA["annotations"],train_size=0.8, random_state=17) 
print(x_train)

[['GFMA appoints Adam Farkas as CEO\r', {'entities': []}], ['"S Pass qualifying salaries to be raised, but workers in some jobs can switch to work permits"\r', {'entities': []}], ['"Rare diseases, common challenges"\r', {'entities': []}], ['"COVID Will Become a Seasonal Disease, Experts Say"\r', {'entities': [[1, 6, 'DISEASE']]}], ["Parkinson's disease: How the brain’s 'recycling system' breaks down\r", {'entities': [[0, 19, 'DISEASE']]}], ['Ukraine crisis: Russian news agency deletes victory editorial\r', {'entities': [[0, 7, 'LOC'], [16, 23, 'NATIONALITY']]}], ['High cholesterol levels: Why taking your medicine diligently is more effective than changing your diet\r', {'entities': []}], ['Nanopore Sequencing Test Can Diagnose 50 Genetic Diseases\r', {'entities': []}], ['Cognito Therapeutics Announces Presentations for Novel Therapeutic in Alzheimer’s Disease at the 2022 American Academy of Neurology (AAN) Conference\r', {'entities': [[70, 89, 'DISEASE'], [102, 148, 'LOC']]}], ['Kenya 

In [5]:
# Add the new labels to ner
for _, annotations in x_train:
  for ent in annotations.get("entities"):
    ner.add_label(ent[2])

In [6]:
pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]
unaffected_pipes = [pipe for pipe in nlp.pipe_names if pipe not in pipe_exceptions]
#import necessary libraries for training

# Begin training by disabling other pipeline components
with nlp.disable_pipes(*unaffected_pipes) :
   sizes = compounding(1.0, 4.0, 1.001)
   # Training for 100 iterations     
   for itn in range(100):
     # shuffle examples before training
     random.shuffle(x_train)
     # batch up the examples using spaCy's minibatch
     batches = minibatch(x_train, size=sizes)
     # dictionary to store losses
     losses = {}
     for batch in batches:
       for text, annotations in batch:
         doc = nlp.make_doc(text)
         example = Example.from_dict(doc, annotations)
         nlp.update([example], drop=0.5, losses=losses)
         print("Losses",losses)

Losses {'ner': 1.9728889308353137}
Losses {'ner': 5.429561069911314}
Losses {'ner': 10.224131773799899}
Losses {'ner': 16.45981459034504}
Losses {'ner': 20.77266256521019}
Losses {'ner': 24.061281262842083}
Losses {'ner': 27.719784028029494}
Losses {'ner': 29.750469700593662}
Losses {'ner': 29.81110184249274}
Losses {'ner': 34.04128600642628}
Losses {'ner': 36.40245863878238}
Losses {'ner': 38.37494273592692}
Losses {'ner': 38.386852678468536}
Losses {'ner': 40.758086027455946}
Losses {'ner': 44.355187905688894}
Losses {'ner': 46.352174127998424}
Losses {'ner': 47.67174120228406}
Losses {'ner': 50.515849271951986}
Losses {'ner': 52.9354184421061}
Losses {'ner': 52.942356182560516}
Losses {'ner': 53.0207792947689}
Losses {'ner': 53.02582379479854}
Losses {'ner': 53.229912301515355}
Losses {'ner': 57.84522717311677}
Losses {'ner': 59.917428942299125}
Losses {'ner': 62.19100251864832}
Losses {'ner': 66.44031930229524}
Losses {'ner': 68.6921522878598}
Losses {'ner': 70.71787415183508}
Loss

Losses {'ner': 449.70066585359206}
Losses {'ner': 451.6422471529893}
Losses {'ner': 451.7394925611401}
Losses {'ner': 453.22514820892275}
Losses {'ner': 453.2531758105391}
Losses {'ner': 468.774068728649}
Losses {'ner': 469.9391501137351}
Losses {'ner': 481.81765121859826}
Losses {'ner': 483.3975013081879}
Losses {'ner': 486.1110723653229}
Losses {'ner': 487.067654721352}
Losses {'ner': 488.30474301868276}
Losses {'ner': 489.0643418797242}
Losses {'ner': 490.9263184437641}
Losses {'ner': 495.07359934435783}
Losses {'ner': 498.217674827619}
Losses {'ner': 501.2041733410767}
Losses {'ner': 504.2186448574989}
Losses {'ner': 504.4110018225889}
Losses {'ner': 507.55460376582175}
Losses {'ner': 508.84814086450746}
Losses {'ner': 509.7426679767341}
Losses {'ner': 514.0297649576274}
Losses {'ner': 514.0541812990978}
Losses {'ner': 517.8127399385407}
Losses {'ner': 519.794770384693}
Losses {'ner': 519.7976002727852}
Losses {'ner': 520.1369343168973}
Losses {'ner': 521.1072135266927}
Losses {'ne

Losses {'ner': 838.2773544740566}
Losses {'ner': 838.4041742036839}
Losses {'ner': 840.7930132107293}
Losses {'ner': 842.288815333166}
Losses {'ner': 846.2880939882735}
Losses {'ner': 847.4300702582501}
Losses {'ner': 849.6980255737026}
Losses {'ner': 851.6646720237202}
Losses {'ner': 853.746199893298}
Losses {'ner': 857.6115819765741}
Losses {'ner': 861.7160419514465}
Losses {'ner': 861.7205040012528}
Losses {'ner': 865.663092561753}
Losses {'ner': 870.38234987605}
Losses {'ner': 871.6509512600816}
Losses {'ner': 871.8182131199726}
Losses {'ner': 872.3878230324132}
Losses {'ner': 873.6791442719689}
Losses {'ner': 875.8484059922214}
Losses {'ner': 877.103135319024}
Losses {'ner': 877.1106833290579}
Losses {'ner': 878.0491665023641}
Losses {'ner': 878.0527768628781}
Losses {'ner': 878.1074862735126}
Losses {'ner': 878.1074862735126}
Losses {'ner': 881.6237353993922}
Losses {'ner': 882.8090339586378}
Losses {'ner': 885.4300690314778}
Losses {'ner': 885.5171921999374}
Losses {'ner': 889.3

Losses {'ner': 174.12242802060373}
Losses {'ner': 177.80253893955182}
Losses {'ner': 177.8025707485253}
Losses {'ner': 182.26875127115702}
Losses {'ner': 184.26723268572383}
Losses {'ner': 184.32341291629203}
Losses {'ner': 184.3267700373512}
Losses {'ner': 184.42379848188605}
Losses {'ner': 184.46719253633427}
Losses {'ner': 186.08366549747535}
Losses {'ner': 188.52622284543776}
Losses {'ner': 188.537260331667}
Losses {'ner': 188.53736041787633}
Losses {'ner': 188.92423574973643}
Losses {'ner': 190.19177423690613}
Losses {'ner': 192.295646618974}
Losses {'ner': 192.29615128261696}
Losses {'ner': 192.29676298936286}
Losses {'ner': 192.29853095622119}
Losses {'ner': 194.5206274717746}
Losses {'ner': 196.51170381340287}
Losses {'ner': 198.10089808965176}
Losses {'ner': 198.1683556044035}
Losses {'ner': 202.3039692143399}
Losses {'ner': 202.3041275780264}
Losses {'ner': 202.30809710509521}
Losses {'ner': 206.30607155366266}
Losses {'ner': 207.5556500850183}
Losses {'ner': 209.534734998670

Losses {'ner': 477.13771159816}
Losses {'ner': 479.465799777021}
Losses {'ner': 479.504134372376}
Losses {'ner': 479.508552332985}
Losses {'ner': 481.108112616093}
Losses {'ner': 482.82498406316165}
Losses {'ner': 482.853709906657}
Losses {'ner': 483.0549829032251}
Losses {'ner': 483.2805797426625}
Losses {'ner': 485.72657737593414}
Losses {'ner': 485.72688649550105}
Losses {'ner': 487.15914756912656}
Losses {'ner': 487.15963352935535}
Losses {'ner': 488.49503902868855}
Losses {'ner': 490.07108375554753}
Losses {'ner': 490.10149403419}
Losses {'ner': 492.725715543097}
Losses {'ner': 493.65230683789855}
Losses {'ner': 495.65608579451157}
Losses {'ner': 500.1883328853139}
Losses {'ner': 500.19016998113307}
Losses {'ner': 500.19225828280236}
Losses {'ner': 504.9710338880802}
Losses {'ner': 506.9276176435758}
Losses {'ner': 506.9278171334502}
Losses {'ner': 510.76401123024436}
Losses {'ner': 512.8835549739748}
Losses {'ner': 519.8651222875128}
Losses {'ner': 521.5680061770863}
Losses {'ner

...

Losses {'ner': 26.466069100951838}
Losses {'ner': 26.466069100951838}
Losses {'ner': 26.466069100951838}
Losses {'ner': 28.245145677184748}
Losses {'ner': 28.245157461953344}
Losses {'ner': 28.245157461953344}
Losses {'ner': 28.245160331434988}
Losses {'ner': 28.245160331434988}
Losses {'ner': 28.245160331434988}
Losses {'ner': 28.24516033143512}
Losses {'ner': 28.245160331435144}
Losses {'ner': 28.245160331435144}
Losses {'ner': 28.245160703831502}
Losses {'ner': 28.245160703950397}
Losses {'ner': 28.245160703950397}
Losses {'ner': 28.245160703950397}
Losses {'ner': 28.245160722965476}
Losses {'ner': 28.245160722965476}
Losses {'ner': 28.245160722965476}
Losses {'ner': 28.245160722965476}
Losses {'ner': 28.245160722985943}
Losses {'ner': 28.245160722986842}
Losses {'ner': 28.24516072298716}
Losses {'ner': 28.24516072298716}
Losses {'ner': 28.761828089014994}
Losses {'ner': 28.761828089114815}
Losses {'ner': 28.76182812999347}
Losses {'ner': 28.762153972171898}
Losses {'ner': 28.762153

Losses {'ner': 42.973242937021595}
Losses {'ner': 42.97324306881421}
Losses {'ner': 42.97324306881421}
Losses {'ner': 42.97324306881421}
Losses {'ner': 42.97324306882676}
Losses {'ner': 42.97324306882884}
Losses {'ner': 42.97324306882884}
Losses {'ner': 42.97324306882884}
Losses {'ner': 42.97324306882895}
Losses {'ner': 42.97324306882905}
Losses {'ner': 42.973243068829056}
Losses {'ner': 42.973243068829056}
Losses {'ner': 42.973243068829056}
Losses {'ner': 42.97324306890199}
Losses {'ner': 42.97324306890199}
Losses {'ner': 42.97324306890199}
Losses {'ner': 42.97324306890199}
Losses {'ner': 42.97324306890199}
Losses {'ner': 42.973243068902015}
Losses {'ner': 42.973243068902015}
Losses {'ner': 42.97324306890208}
Losses {'ner': 42.97324306890208}
Losses {'ner': 42.97324306890208}
Losses {'ner': 42.97324306890479}
Losses {'ner': 42.973243068907934}
Losses {'ner': 42.973243068907934}
Losses {'ner': 42.97324306964997}
Losses {'ner': 42.97324306964997}
Losses {'ner': 42.97324306964997}
Losses

Losses {'ner': 10.536155126256112}
Losses {'ner': 10.536155126261393}
Losses {'ner': 10.536155126261393}
Losses {'ner': 14.514214656519572}
Losses {'ner': 14.514214656528585}
Losses {'ner': 14.514214656528656}
Losses {'ner': 14.514214656531731}
Losses {'ner': 14.514214656531733}
Losses {'ner': 14.514214656531733}
Losses {'ner': 14.514214656539663}
Losses {'ner': 14.514215475522517}
Losses {'ner': 14.514215475522517}
Losses {'ner': 14.514234771711847}
Losses {'ner': 14.514234771726423}
Losses {'ner': 14.514234771764794}
Losses {'ner': 14.514234771764794}
Losses {'ner': 14.514247636695059}
Losses {'ner': 14.514247636695059}
Losses {'ner': 14.514247636695066}
Losses {'ner': 14.514247636695183}
Losses {'ner': 14.514247636695183}
Losses {'ner': 14.514247636824578}
Losses {'ner': 14.51424763683026}
Losses {'ner': 14.51424763683026}
Losses {'ner': 14.514247636830271}
Losses {'ner': 14.514247636830271}
Losses {'ner': 14.514247636933812}
Losses {'ner': 14.514249869240384}
Losses {'ner': 14.5142

Losses {'ner': 36.474315797459575}
Losses {'ner': 36.47431624884191}
Losses {'ner': 36.47431624884191}
Losses {'ner': 36.47431624884191}
Losses {'ner': 36.47431628812299}
Losses {'ner': 36.47431628812793}
Losses {'ner': 36.47431628812801}
Losses {'ner': 36.47431628812801}
Losses {'ner': 36.47431628812801}
Losses {'ner': 36.47431628812801}
Losses {'ner': 36.47431628812801}
Losses {'ner': 38.476733839490805}
Losses {'ner': 38.476733839490805}
Losses {'ner': 38.476733839490805}
Losses {'ner': 38.4767564851664}
Losses {'ner': 38.4767564851664}
Losses {'ner': 38.47675656033026}
Losses {'ner': 38.47675656033026}
Losses {'ner': 38.47675656033026}
Losses {'ner': 38.47675656033026}
Losses {'ner': 38.47675656033038}
Losses {'ner': 38.47675656033038}
Losses {'ner': 38.476756560330394}
Losses {'ner': 38.476756560330394}
Losses {'ner': 38.476756560330394}
Losses {'ner': 38.47675664600188}
Losses {'ner': 38.47675667864466}
Losses {'ner': 38.47675667865281}
Losses {'ner': 38.47675667875545}
Losses {'

Losses {'ner': 45.95560670838084}
Losses {'ner': 45.95560670838084}
Losses {'ner': 45.95560670838084}
Losses {'ner': 45.95560670838084}
Losses {'ner': 45.95560670838084}
Losses {'ner': 46.32360398963418}
Losses {'ner': 46.56196284488168}
Losses {'ner': 46.56196284488168}
Losses {'ner': 46.56196284488168}
Losses {'ner': 46.56196284488168}
Losses {'ner': 46.56196284488168}
Losses {'ner': 46.892099134749316}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474944}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner': 46.89209913474945}
Losses {'ner'

In [8]:
def evaluate(ner_model, samples):
    scorer = Scorer(ner_model)
    example = []
    for text, sample in samples:
        pred = ner_model(text)
        #print(pred, sample['entities'])
        temp_ex = Example.from_dict(pred, {'entities': sample['entities']})
        example.append(temp_ex)
    scores = scorer.score(example)
    
    return scores

In [9]:
# ner_model = spacy.load(ner_model_path) # for spaCy's pretrained use 'en_core_web_sm'
results = evaluate(nlp, x_test)
print(results)

{'token_acc': 1.0, 'token_p': 1.0, 'token_r': 1.0, 'token_f': 1.0, 'tag_acc': None, 'sents_p': None, 'sents_r': None, 'sents_f': None, 'dep_uas': None, 'dep_las': None, 'dep_las_per_type': None, 'pos_acc': None, 'morph_acc': None, 'morph_micro_p': None, 'morph_micro_r': None, 'morph_micro_f': None, 'morph_per_feat': None, 'lemma_acc': None, 'ents_p': 0.7209302325581395, 'ents_r': 0.6549295774647887, 'ents_f': 0.6863468634686347, 'ents_per_type': {'DISEASE': {'p': 0.7761194029850746, 'r': 0.6753246753246753, 'f': 0.7222222222222222}, 'LOC': {'p': 0.6730769230769231, 'r': 0.6363636363636364, 'f': 0.6542056074766355}, 'NATIONALITY': {'p': 0.6, 'r': 0.6, 'f': 0.6}}}


In [10]:
nlp2=spacy.load('en_core_web_sm')
# Getting the pipeline component for ner
ner2=nlp2.get_pipe("ner")
ner2

In [11]:
with open("annotations (2).json",'r', encoding="utf8") as f:
    TRAIN_DATA2 = json.load(f)
    print(TRAIN_DATA2)

{'classes': ['DISEASE'], 'annotations': [['Objective disease activity assessment and therapeutic drug monitoring prior to biologic therapy changes in routine inflammatory bowel disease clinical practice: TARGET-IBD - BMC Gastroenterology\r', {'entities': [[115, 141, 'DISEASE']]}], ["Crohn's disease and dietary fiber: What is the link?\r", {'entities': [[0, 15, 'DISEASE']]}], ["Northampton parents' plea over toddler with rare disease\r", {'entities': []}], ['"\'Door has been opened\' with Rare Disease Drug Strategy, says advocate"\r', {'entities': []}], ['Is IBD an Autoimmune Disease?\r', {'entities': [[3, 6, 'DISEASE'], [10, 28, 'DISEASE']]}], ['EXCLUSIVE WHO says it advised Ukraine to destroy pathogens in health labs to prevent disease spread\r', {'entities': []}], ['"Nutrition is the number one cause of disease, cardiologist says"\r', {'entities': []}], ['Cholesterol And Heart Disease: Is There A Connection?\r', {'entities': [[0, 11, 'DISEASE'], [16, 29, 'DISEASE']]}], ['The Joy of C

In [12]:
x_train ,x_test = train_test_split(TRAIN_DATA2["annotations"],train_size=0.8, random_state=17) 
print(x_train)

[['GFMA appoints Adam Farkas as CEO\r', {'entities': []}], ['"S Pass qualifying salaries to be raised, but workers in some jobs can switch to work permits"\r', {'entities': []}], ['"Rare diseases, common challenges"\r', {'entities': []}], ['"COVID Will Become a Seasonal Disease, Experts Say"\r', {'entities': [[1, 6, 'DISEASE']]}], ["Parkinson's disease: How the brain’s 'recycling system' breaks down\r", {'entities': [[0, 19, 'DISEASE']]}], ['Ukraine crisis: Russian news agency deletes victory editorial\r', {'entities': []}], ['High cholesterol levels: Why taking your medicine diligently is more effective than changing your diet\r', {'entities': []}], ['Nanopore Sequencing Test Can Diagnose 50 Genetic Diseases\r', {'entities': []}], ['Cognito Therapeutics Announces Presentations for Novel Therapeutic in Alzheimer’s Disease at the 2022 American Academy of Neurology (AAN) Conference\r', {'entities': [[70, 89, 'DISEASE']]}], ['Kenya on high alert after Tanzania reports Marburg disease outb

In [13]:
# Add the new labels to ner
for _, annotations in x_train:
  for ent in annotations.get("entities"):
    ner2.add_label(ent[2])

In [15]:
pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]
unaffected_pipes = [pipe for pipe in nlp2.pipe_names if pipe not in pipe_exceptions]
#import necessary libraries for training

# Begin training by disabling other pipeline components
with nlp2.disable_pipes(*unaffected_pipes) :
   sizes = compounding(1.0, 4.0, 1.001)
   # Training for 100 iterations     
   for itn in range(100):
     # shuffle examples before training
     random.shuffle(x_train)
     # batch up the examples using spaCy's minibatch
     batches = minibatch(x_train, size=sizes)
     # dictionary to store losses
     losses = {}
     for batch in batches:
       for text, annotations in batch:
         doc = nlp2.make_doc(text)
         example = Example.from_dict(doc, annotations)
         nlp2.update([example], drop=0.5, losses=losses)
         print("Losses",losses)

Losses {'ner': 4.061805409753022}
Losses {'ner': 9.113550195121578}
Losses {'ner': 9.235492219273528}
Losses {'ner': 13.283466054522483}
Losses {'ner': 13.285668761049712}
Losses {'ner': 20.627827229341612}
Losses {'ner': 24.162162386336767}
Losses {'ner': 31.074866569707357}
Losses {'ner': 32.84742779570297}
Losses {'ner': 36.90383526414691}
Losses {'ner': 38.73001522835288}
Losses {'ner': 40.73432928550688}
Losses {'ner': 40.76855498694964}
Losses {'ner': 40.76879908561195}
Losses {'ner': 41.82933491464128}
Losses {'ner': 42.22293536628984}
Losses {'ner': 47.10470099417236}
Losses {'ner': 48.336255860250304}
Losses {'ner': 50.33636484866267}
Losses {'ner': 56.92937988977134}
Losses {'ner': 58.79833556992146}
Losses {'ner': 58.80912420342796}
Losses {'ner': 59.659290056624215}
Losses {'ner': 59.66266981350629}
Losses {'ner': 59.666064886822475}
Losses {'ner': 61.67227618865079}
Losses {'ner': 61.67237196315689}
Losses {'ner': 63.392861724274944}
Losses {'ner': 65.40712644294159}
Losse

Losses {'ner': 342.19616467241093}
Losses {'ner': 346.09539509888646}
Losses {'ner': 346.2036222222731}
Losses {'ner': 347.4037983759558}
Losses {'ner': 350.8614234350354}
Losses {'ner': 352.695594823699}
Losses {'ner': 354.64284921084766}
Losses {'ner': 354.69400496489436}
Losses {'ner': 356.1407524077665}
Losses {'ner': 356.14579731250035}
Losses {'ner': 357.8243406926009}
Losses {'ner': 359.21423280688856}
Losses {'ner': 363.1545255177533}
Losses {'ner': 363.2563636135819}
Losses {'ner': 363.2600508021676}
Losses {'ner': 363.2698440729251}
Losses {'ner': 366.00373138720056}
Losses {'ner': 366.01021315589225}
Losses {'ner': 366.02646782212156}
Losses {'ner': 367.9204012042273}
Losses {'ner': 390.6584380751837}
Losses {'ner': 390.66679336074213}
Losses {'ner': 392.5805380139224}
Losses {'ner': 393.6090752210505}
Losses {'ner': 394.430000139907}
Losses {'ner': 394.5946841824496}
Losses {'ner': 394.5952257684184}
Losses {'ner': 396.51526663046275}
Losses {'ner': 399.84136687061346}
Loss

Losses {'ner': 611.2820184889525}
Losses {'ner': 613.2014432750823}
Losses {'ner': 615.1784188266729}
Losses {'ner': 615.1784200296976}
Losses {'ner': 615.1795243567739}
Losses {'ner': 615.1863945994028}
Losses {'ner': 617.0322220413813}
Losses {'ner': 617.0322415614603}
Losses {'ner': 617.0322440892511}
Losses {'ner': 619.0283411987679}
Losses {'ner': 619.1736187483074}
Losses {'ner': 619.1743095400973}
Losses {'ner': 619.7799842866546}
Losses {'ner': 619.7801338519658}
Losses {'ner': 619.7805169909716}
Losses {'ner': 619.7845694776832}
Losses {'ner': 619.8131772514072}
Losses {'ner': 619.8132163606923}
Losses {'ner': 619.8139263668809}
Losses {'ner': 621.8296412106299}
Losses {'ner': 621.8396631981869}
Losses {'ner': 621.8417569154229}
Losses {'ner': 621.8417750254149}
Losses {'ner': 621.8428764377152}
Losses {'ner': 623.842809193709}
Losses {'ner': 623.8428158783212}
Losses {'ner': 623.8431126453388}
Losses {'ner': 623.8432815856573}
Losses {'ner': 623.8435655434121}
Losses {'ner': 

Losses {'ner': 114.99080635761455}
Losses {'ner': 116.8071483080099}
Losses {'ner': 116.8078056715818}
Losses {'ner': 116.8096229904748}
Losses {'ner': 120.80226793827585}
Losses {'ner': 124.81102349926367}
Losses {'ner': 126.69194498099549}
Losses {'ner': 130.82957736556696}
Losses {'ner': 133.18274653567624}
Losses {'ner': 135.78678149655403}
Losses {'ner': 137.681189543242}
Losses {'ner': 137.71422624997152}
Losses {'ner': 137.72318564451535}
Losses {'ner': 137.76289559011275}
Losses {'ner': 140.00145400447715}
Losses {'ner': 140.00211415707463}
Losses {'ner': 140.98973656366923}
Losses {'ner': 141.00059617855467}
Losses {'ner': 142.65175156364617}
Losses {'ner': 142.66323772407895}
Losses {'ner': 142.7465273281201}
Losses {'ner': 142.7485780396594}
Losses {'ner': 144.65152982196685}
Losses {'ner': 146.62533498965263}
Losses {'ner': 146.62535976174505}
Losses {'ner': 146.63758135444553}
Losses {'ner': 148.63472701049227}
Losses {'ner': 150.63954611025633}
Losses {'ner': 152.54468248

Losses {'ner': 364.55497271971}
Losses {'ner': 364.6442488844673}
Losses {'ner': 365.5524549327327}
Losses {'ner': 365.55749289770546}
Losses {'ner': 365.65840534302913}
Losses {'ner': 365.671799875203}
Losses {'ner': 366.22411680605967}
Losses {'ner': 368.0861722919506}
Losses {'ner': 368.08625027376326}
Losses {'ner': 368.09951892196534}
Losses {'ner': 368.52166291361334}
Losses {'ner': 368.5899595080459}
Losses {'ner': 368.608390343068}
Losses {'ner': 368.6089906663667}
Losses {'ner': 368.6092546742819}
Losses {'ner': 368.61072634316514}
Losses {'ner': 368.61183883835645}
Losses {'ner': 368.6119545634674}
Losses {'ner': 368.6120912046466}
Losses {'ner': 370.6053730697327}
Losses {'ner': 370.60538042523046}
Losses {'ner': 370.61463086686854}
Losses {'ner': 374.5275672518681}
Losses {'ner': 374.56155087337135}
Losses {'ner': 374.56155478829805}
Losses {'ner': 374.86440653872324}
Losses {'ner': 374.86440891290925}
Losses {'ner': 374.88510844840744}
Losses {'ner': 375.24986102862044}
Lo

...

Losses {'ner': 1.6449794942298792}
Losses {'ner': 1.64497949430562}
Losses {'ner': 1.8045336330853705}
Losses {'ner': 1.8045336330854653}
Losses {'ner': 1.8045336330854653}
Losses {'ner': 1.8045336334823248}
Losses {'ner': 1.8045336334824897}
Losses {'ner': 1.8045336334825057}
Losses {'ner': 1.8045336334825057}
Losses {'ner': 1.8045336334825057}
Losses {'ner': 1.804586957306028}
Losses {'ner': 1.804586957306028}
Losses {'ner': 1.804586957306028}
Losses {'ner': 1.804586957306028}
Losses {'ner': 1.8045869573061335}
Losses {'ner': 1.8045869573061335}
Losses {'ner': 1.8045869573061735}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306182}
Losses {'ner': 1.804586957306205}
Losses {'ner': 1.80458695732358}
Losses {'ner': 1.8045869573235802}
Losses {'ner': 1.8045869573235822}
Losses {'ner': 1.8045869573235822}
Losses {'ner': 1.8045869573235822}


Losses {'ner': 7.836928600586393}
Losses {'ner': 7.836928600587647}
Losses {'ner': 7.836928600587647}
Losses {'ner': 7.836928600587647}
Losses {'ner': 7.836928600587647}
Losses {'ner': 7.836928600587647}
Losses {'ner': 7.8369286005876475}
Losses {'ner': 7.836928600587666}
Losses {'ner': 7.836928600587667}
Losses {'ner': 7.836928600587667}
Losses {'ner': 7.836928600587667}
Losses {'ner': 7.836928600587667}
Losses {'ner': 7.836928600966258}
Losses {'ner': 7.836928600966258}
Losses {'ner': 7.836928600966272}
Losses {'ner': 7.836928600966272}
Losses {'ner': 7.836928600966272}
Losses {'ner': 7.836928600966284}
Losses {'ner': 7.836928600966311}
Losses {'ner': 7.836928600966311}
Losses {'ner': 7.836928600966311}
Losses {'ner': 7.836928600966312}
Losses {'ner': 7.836928600966312}
Losses {'ner': 7.836928669076224}
Losses {'ner': 7.836928669076224}
Losses {'ner': 7.836928678033362}
Losses {'ner': 7.836928678033362}
Losses {'ner': 7.836928678033362}
Losses {'ner': 7.836928678033362}
Losses {'ner'

Losses {'ner': 19.11788269031119}
Losses {'ner': 19.11788269031119}
Losses {'ner': 19.11788269031119}
Losses {'ner': 19.11788269031119}
Losses {'ner': 19.11788269031119}
Losses {'ner': 19.117988791233486}
Losses {'ner': 19.117988791233486}
Losses {'ner': 19.117988791233486}
Losses {'ner': 19.118206914634804}
Losses {'ner': 19.118206914634804}
Losses {'ner': 19.620774384708504}
Losses {'ner': 19.620774384708522}
Losses {'ner': 19.62078617195358}
Losses {'ner': 19.62078617195358}
Losses {'ner': 19.62078617195358}
Losses {'ner': 21.62071440796127}
Losses {'ner': 21.620714408214575}
Losses {'ner': 21.620714408214575}
Losses {'ner': 21.620714408214575}
Losses {'ner': 21.620714408214575}
Losses {'ner': 21.620714408214575}
Losses {'ner': 21.620714408214575}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.472724419887548}
Losses {'ner': 23.47272441988

Losses {'ner': 3.8625251747803055}
Losses {'ner': 3.8625251747803055}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.862525174818477}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185256}
Losses {'ner': 3.8625251748185283}
Losses {'ner': 3.8625251748185283}
Losses {'ner': 4.162512848577989}
Losses {'ner': 4.162512848585528}
Losses {'ner': 4.162512848585528}
Losses {'ner': 4.162512848585528}
Losses {'ner': 4.16251284858575}
Losses {'ner': 4.16251284858575}
Losses {'ner': 4.162512848586814}
Lo

Losses {'ner': 13.471593381721771}
Losses {'ner': 13.471593381721771}
Losses {'ner': 13.471593381721771}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.471593381722707}
Losses {'ner': 13.477872167599637}
Losses {'ner': 13.477872167599637}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167599672}
Losses {'ner': 13.477872167602184}
Losses {'ner': 15.477872167620776}
Losses {'ner': 15.477872167620776}
Losses {'ner': 15.477872167620776}
Losses {'ner': 15.477872167620776}
Losses {'ner': 15.477872167620776}
Losses {'ner': 15.477872167620776}
Losses {'ner': 17.477824841532822}
Losses {'ner': 17.47

In [16]:
# ner_model = spacy.load(ner_model_path) # for spaCy's pretrained use 'en_core_web_sm'
results2 = evaluate(nlp2, x_test)
print(results2)

{'token_acc': 1.0, 'token_p': 1.0, 'token_r': 1.0, 'token_f': 1.0, 'tag_acc': None, 'sents_p': None, 'sents_r': None, 'sents_f': None, 'dep_uas': None, 'dep_las': None, 'dep_las_per_type': None, 'pos_acc': None, 'morph_acc': None, 'morph_micro_p': None, 'morph_micro_r': None, 'morph_micro_f': None, 'morph_per_feat': None, 'lemma_acc': None, 'ents_p': 0.7808219178082192, 'ents_r': 0.7307692307692307, 'ents_f': 0.7549668874172185, 'ents_per_type': {'DISEASE': {'p': 0.7808219178082192, 'r': 0.7402597402597403, 'f': 0.7600000000000001}, 'Unlabelled': {'p': 0.0, 'r': 0.0, 'f': 0.0}}}


In [17]:
# Save NER model
pickle.dump(nlp, open('ner_model_multi_train.pkl', 'wb'))
pickle.dump(nlp2,open('ner_model_disease.pkl','wb'))

In [ ]:
# # Load NER model
# ner_model = pickle.load(open('ner_model_disease.pkl', 'rb'))

In [ ]:
# for i,l in x_test:
#     doc = nlp(i)
#     print("Entities", [(ent.text, ent.label_) for ent in doc.ents])